In [1]:
!pip install networkx
!pip install ipywidgets

In [2]:
import os
import sys
import runpy
import time
import numpy as np
import pandas as pd
import random
import argparse
import networkx as nx

from collections import deque
from IPython.display import Image
from IPython.display import HTML

import matplotlib.pyplot as plt
import matplotlib.animation as animation
from matplotlib.colors import ListedColormap
from matplotlib.patches import Rectangle, Patch, Circle
from matplotlib.widgets import Button, Slider
from matplotlib.lines import Line2D

from ipywidgets import interact, IntSlider
import ipywidgets as widgets

# Env file

In [3]:
class Robot: 
    def __init__(self, position): 
        self.position = position
        self.carrying = 0

class Package: 
    def __init__(self, start, start_time, target, deadline, package_id): 
        self.start = start
        self.start_time = start_time
        self.target = target
        self.deadline = deadline
        self.package_id = package_id
        self.status = 'None' # Possible statuses: 'waiting', 'in_transit', 'delivered'

class Environment: 

    def __init__(self, map_file, max_time_steps = 100, n_robots = 5, n_packages=20,
             move_cost=-0.01, delivery_reward=10., delay_reward=1., 
             seed=2025): 
        """ Initializes the simulation environment. :param map_file: Path to the map text file. :param move_cost: Cost incurred when a robot moves (LRUD). :param delivery_reward: Reward for delivering a package on time. """ 
        self.map_file = map_file
        self.grid = self.load_map()
        self.n_rows = len(self.grid)
        self.n_cols = len(self.grid[0]) if self.grid else 0 
        self.move_cost = move_cost 
        self.delivery_reward = delivery_reward 
        self.delay_reward = delay_reward
        self.t = 0 
        self.robots = [] # List of Robot objects.
        self.packages = [] # List of Package objects.
        self.total_reward = 0

        self.n_robots = n_robots
        self.max_time_steps = max_time_steps
        self.n_packages = n_packages

        self.rng = np.random.RandomState(seed)
        self.reset()
        self.done = False
        self.state = None

    def load_map(self):
        """
        Reads the map file and returns a 2D grid.
        Assumes that each line in the file contains numbers separated by space.
        0 indicates free cell and 1 indicates an obstacle.
        """
        grid = []
        with open(self.map_file, 'r') as f:
            for line in f:
                # Strip line breaks and split into numbers
                row = [int(x) for x in line.strip().split(' ')]
                grid.append(row)
        return grid
    
    def is_free_cell(self, position):
        """
        Checks if the cell at the given position is free (0) or occupied (1).
        :param position: Tuple (row, column) to check.
        :return: True if the cell is free, False otherwise.
        """
        r, c = position
        if r < 0 or r >= self.n_rows or c < 0 or c >= self.n_cols:
            return False
        return self.grid[r][c] == 0

    def add_robot(self, position):
        """
        Adds a robot at the given position if the cell is free.
        :param position: Tuple (row, column) for the robot's starting location.
        """
        if self.is_free_cell(position):
            robot = Robot(position)
            self.robots.append(robot)
        else:
            raise ValueError("Invalid robot position: must be on a free cell not occupied by an obstacle or another robot.")

    def reset(self):
        """
        Resets the environment to its initial state.
        Clears all robots and packages, and reinitializes the grid.
        """
        self.t = 0
        self.robots = []
        self.packages = []
        self.total_reward = 0
        self.done = False
        self.state = None

        # Reinitialize the grid
        #self.grid = self.load_map(sel)
        # Add robots and packages
        tmp_grid = np.array(self.grid)
        for i in range(self.n_robots):
            # Randomly select a free cell for the robot
            position, tmp_grid = self.get_random_free_cell(tmp_grid)
            self.add_robot(position)
        
        N = self.n_rows
        list_packages = []
        for i in range(self.n_packages):
            # Randomly select a free cell for the package
            start = self.get_random_free_cell_p()
            while True:
                target = self.get_random_free_cell_p()
                if start != target:
                    break
            
            to_deadline = 10 + self.rng.randint(N/2, 3*N)
            if i <= min(self.n_robots, 20):
                start_time = 0
            else:
                start_time = self.rng.randint(1, self.max_time_steps)
            list_packages.append((start_time, start, target, start_time + to_deadline ))

        list_packages.sort(key=lambda x: x[0])
        for i in range(self.n_packages):
            start_time, start, target, deadline = list_packages[i]
            package_id = i+1
            self.packages.append(Package(start, start_time, target, deadline, package_id))

        return self.get_state()
    
    def get_state(self):
        """
        Returns the current state of the environment.
        The state includes the positions of robots and packages.
        :return: State representation.
        """
        selected_packages = []
        for i in range(len(self.packages)):
            if self.packages[i].start_time == self.t:
                selected_packages.append(self.packages[i])
                self.packages[i].status = 'waiting'

        state = {
            'time_step': self.t,
            'map': self.grid,
            'robots': [(robot.position[0] + 1, robot.position[1] + 1,
                        robot.carrying) for robot in self.robots],
            'packages': [(package.package_id, package.start[0] + 1, package.start[1] + 1, 
                          package.target[0] + 1, package.target[1] + 1, package.start_time, package.deadline) for package in selected_packages]
        }
        return state
        

    def get_random_free_cell_p(self):
        """
        Returns a random free cell in the grid.
        :return: Tuple (row, col) of a free cell.
        """
        free_cells = [(i, j) for i in range(self.n_rows) for j in range(self.n_cols) \
                      if self.grid[i][j] == 0]
        i = self.rng.randint(0, len(free_cells))
        return free_cells[i]


    def get_random_free_cell(self, new_grid):
        """
        Returns a random free cell in the grid.
        :return: Tuple (row, col) of a free cell.
        """
        free_cells = [(i, j) for i in range(self.n_rows) for j in range(self.n_cols) \
                      if new_grid[i][j] == 0]
        i = self.rng.randint(0, len(free_cells))
        new_grid[free_cells[i][0]][free_cells[i][1]] = 1
        return free_cells[i], new_grid

    
    def step(self, actions):
        """
        Advances the simulation by one timestep.
        :param actions: A list where each element is a tuple (move_action, package_action) for a robot.
            move_action: one of 'S', 'L', 'R', 'U', 'D'.
            package_action: '1' (pickup), '2' (drop), or '0' (do nothing).
        :return: The updated state and total accumulated reward.
        """
        r = 0
        if len(actions) != len(self.robots):
            raise ValueError("The number of actions must match the number of robots.")

        # -------- Process Movement --------
        proposed_positions = []
        # For each robot, compute the new position based on the movement action.
        old_pos = {}
        next_pos = {}
        for i, robot in enumerate(self.robots):
            move, pkg_act = actions[i]
            new_pos = self.compute_new_position(robot.position, move)
            # Check if the new position is valid (inside bounds and not an obstacle).
            if not self.valid_position(new_pos):
                new_pos = robot.position  # Invalid moves result in no change.
            proposed_positions.append(new_pos)
            old_pos[robot.position] = i
            next_pos[new_pos] = i

        moved_robots = [0 for _ in range(len(self.robots))]
        computed_moved = [0 for _ in range(len(self.robots))]
        final_positions = [None] * len(self.robots)
        occupied = {}  # Dictionary to record occupied cells.
        while True:
            updated = False
            for i in range(len(self.robots)):
            
                if computed_moved[i] != 0: 
                    continue

                pos = self.robots[i].position
                new_pos = proposed_positions[i]
                can_move = False
                if new_pos not in old_pos:
                    can_move = True
                else:
                    j = old_pos[new_pos]
                    if (j != i) and (computed_moved[j] == 0): # We must wait for the conflict resolve
                        continue
                    # We can decide where the robot can go now
                    can_move = True

                if can_move:
                    if new_pos not in occupied:
                        occupied[new_pos] = i
                        final_positions[i] = new_pos
                        computed_moved[i] = 1
                        moved_robots[i] = 1
                        updated = True
                    else:
                        new_pos = pos
                        occupied[new_pos] = i
                        final_positions[i] = pos
                        computed_moved[i] = 1
                        moved_robots[i] = 0
                        updated = True

                if updated:
                    break

            if not updated:
                break
        for i in range(len(self.robots)):
            if computed_moved[i] == 0:
                final_positions[i] = self.robots[i].position 
        
        # Update robot positions and apply movement cost when applicable.
        for i, robot in enumerate(self.robots):
            move, pkg_act = actions[i]
            if move in ['L', 'R', 'U', 'D'] and final_positions[i] != robot.position:
                r += self.move_cost
            robot.position = final_positions[i]

        # -------- Process Package Actions --------
        for i, robot in enumerate(self.robots):
            move, pkg_act = actions[i]
            # Pick up action.
            if pkg_act == '1':
                if robot.carrying == 0:
                    # Check for available packages at the current cell.
                    for j in range(len(self.packages)):
                        if self.packages[j].status == 'waiting' and self.packages[j].start == robot.position and self.packages[j].start_time <= self.t:
                            # Pick the package with the smallest package_id.
                            package_id = self.packages[j].package_id
                            robot.carrying = package_id
                            self.packages[j].status = 'in_transit'
                            break

            # Drop action.
            elif pkg_act == '2':
                if robot.carrying != 0:
                    package_id = robot.carrying
                    target = self.packages[package_id - 1].target
                    # Check if the robot is at the target position.
                    if robot.position == target:
                        # Update package status to delivered.
                        pkg = self.packages[package_id - 1]
                        pkg.status = 'delivered'
                        # Apply reward based on whether the delivery is on time.
                        if self.t <= pkg.deadline:
                            r += self.delivery_reward
                        else:
                            # Example: a reduced reward for late delivery.
                            r += self.delay_reward
                        robot.carrying = 0  
        
        # Increment the simulation timestep.
        self.t += 1

        self.total_reward += r

        done = False
        infos = {}
        if self.check_terminate():
            done = True
            infos['total_reward'] = self.total_reward
            infos['total_time_steps'] = self.t

        return self.get_state(), r, done, infos
    
    def check_terminate(self):
        if self.t == self.max_time_steps:
            return True
        
        for p in self.packages:
            if p.status != 'delivered':
                return False
            
        return True

    def compute_new_position(self, position, move):
        """
        Computes the intended new position for a robot given its current position and move command.
        """
        r, c = position
        if move == 'S':
            return (r, c)
        elif move == 'L':
            return (r, c - 1)
        elif move == 'R':
            return (r, c + 1)
        elif move == 'U':
            return (r - 1, c)
        elif move == 'D':
            return (r + 1, c)
        else:
            return (r, c)

    def valid_position(self, pos):
        """
        Checks if the new position is within the grid and not an obstacle.
        """
        r, c = pos
        if r < 0 or r >= self.n_rows or c < 0 or c >= self.n_cols:
            return False
        if self.grid[r][c] == 1:
            return False
        return True

    def render(self):
        """
        A simple text-based rendering of the map showing obstacles and robot positions.
        Obstacles are represented by 1, free cells by 0, and robots by 'R'.
        """
        # Make a deep copy of the grid
        grid_copy = [row[:] for row in self.grid]
        for i, robot in enumerate(self.robots):
            r, c = robot.position
            grid_copy[r][c] = 'R%i'%i
        for row in grid_copy:
            print('\t'.join(str(cell) for cell in row))

# Functions

In [4]:
# Các vị trí các ô trên board, vị trí robots, packages đều tính từ 1

# Tính vị trí hợp lệ của bước đi
def compute_valid_position(map, position, move):
    r, c = position
    if move == 'S':
        i, j = r, c
    elif move == 'L':
        i, j = r, c - 1
    elif move == 'R':
        i, j = r, c + 1
    elif move == 'U':
        i, j = r - 1, c
    elif move == 'D':
        i, j = r + 1, c
    else:
        i, j = r, c
    if i <= 1 or i >= len(map) or j <= 1 or j >= len(map[0]):
        return r, c
    if map[i-1][j-1] == 1:
        return r, c
    return i, j

# Kiểm tra 1 vị trí có hợp lệ không (ô chứa số 0 trên board)
def valid_position(map, position):
    i, j = position
    if i <= 1 or i >= len(map) or j <= 1 or j >= len(map[0]):
        return False
    if map[i-1][j-1] == 1:
        return False
    return True

# Tìm tất cả chu trình sẽ xuất hiện từ các actions thực hiện

def find_all_cycle(map, robots, actions):
    visited = {}
    pos_current = {}
    pos_future = {}

    for i in range(len(robots)):
        pos_robot = (robots[i][0], robots[i][1])
        pos_current[i] = pos_robot
        visited[pos_robot] = False
        next_pos = compute_valid_position(map, pos_robot, actions[i][0])
        pos_future[pos_robot] = next_pos

    list_cycles = []
    list_actions = []

    # Xét các thành phần liên thông
    # Kết quả dễ nhận thấy: Các thành phần chu trình sẽ ở các thành phần liên thông khác nhau
    # Hay mỗi thành phần liên thông chỉ có nhiều nhất một chu trình
    for i in range(len(robots)):
        queue = deque()
        if not visited[pos_current[i]]:
            queue.append(pos_current[i])
            visited[pos_current[i]] = True

        start_pos = None
        history = [pos_current[i]] # Lưu những vị trí đã xuất hiện trong thành phần liên thông này

        while queue:
            start = queue.popleft()
            target = pos_future[start]

            # Thoát luôn vì vị trí này không thể tạo nên chu trình
            # Vì vị trí định đi tới không trùng với vị trí đang có robots đứng
            # Vì chỉ có duy nhất 1 đường đi ra từ mỗi node nên không thể có nhiều hơn 1 nhánh
            if target not in visited:
                break

            if not visited[target]:
                queue.append(target)
                visited[target] = True
                history.append(target)
            else:
                # Nếu vị trí định tới đã được lưu thì đã tồn tại chu trình
                # Thoát luôn vì dù sao cũng không thể còn cạnh nào nữa
                if target in history and target != start:
                    start_pos = target
                break

        cycle = []
        action =[]

        # Nếu tồn tại chu trình thì truy ngược lại toàn bộ chu trình đó
        while start_pos:
            # Nếu node được duyệt lại là đã tìm được đầy đủ chu trình
            if start_pos in cycle:
                break

            # Chỉ cần tìm robot duy nhất đứng tại vị trí xác định
            for j in range(len(robots)):
                if start_pos == (robots[j][0], robots[j][1]):
                    action.append(actions[j])
                    break

            cycle.append(start_pos)
            start_pos = pos_future[start_pos]

        # Nếu có chu trình thì lưu lại thứ tự các robot và các action tạo nên chu trình
        # => Để tìm cách giải quyết
        if len(cycle) > 0:
            list_cycles.append(cycle)
            list_actions.append(action)

    return list_cycles, list_actions

# Tìm 1 đường đi ngắn nhất giữa 2 ô không bị chặn (2 ô phân biệt chứa sô 0 trên board)
def get_shortest_path(map):
    list_path = {}
    valid_pos = []
    m, n = len(map), len(map[0])
    directions = [("U", (-1, 0)), ("L", (0, -1)), ("R", (0, 1)), ("D", (1, 0))]

    # Lưu những vị trí không bị chặn
    for i in range(m):
        for j in range(n):
            if map[i][j] == 0:
                valid_pos.append((i, j))

    # Tại mỗi vị trí không bị chặn, dùng BFS để tìm đường đi ngắn nhất tới tất cả các vị trí khác
    for i in range(len(valid_pos)):
        dist = [[-1] * n for _ in range(m)] # Mảng 2 chiều đánh dấu những vị trí được xét hay chưa (nếu = 0)
        str_path = [[""] * n for _ in range(m)] # Mảng 2 chiều lưu đường đi từ vị trí xét đến vị trí hiện tại
        # Có thể xử lý theo lưu tất cả đường có thể, để sau có chiến thuật lựa chọn nào đó

        queue = deque()
        queue.append(valid_pos[i])

        start_i, start_j = valid_pos[i]
        dist[start_i][start_j] = 0
        str_path[start_i][start_j] = ""

        while queue:
            x, y = queue.popleft()

            # random.shuffle(directions) # có thể shuffle lên để tìm kiếm những hướng đi mới
            for (direc_move, (d_x, d_y)) in directions:
                pos_x = x + d_x
                pos_y = y + d_y
                if 0 < pos_x < m and 0 < pos_y < n and dist[pos_x][pos_y] == -1:
                    if map[pos_x][pos_y] == 0:
                        dist[pos_x][pos_y] = dist[x][y] + 1
                        str_path[pos_x][pos_y] = str_path[x][y] + direc_move
                        queue.append((pos_x, pos_y))

                        start = (start_i + 1, start_j + 1)
                        target = (pos_x + 1, pos_y + 1)
                        list_path[(start, target)] = str_path[pos_x][pos_y]
    return list_path

# GreedyAgent

In [5]:
# import numpy as np
# Run a BFS to find the path from start to goal
def run_bfs(map, start, goal):
    n_rows = len(map)
    n_cols = len(map[0])

    queue = []
    visited = set()
    queue.append((goal, []))
    visited.add(goal)
    d = {}
    d[goal] = 0

    while queue:
        current, path = queue.pop(0)

        for dx, dy in [(-1, 0), (1, 0), (0, -1), (0, 1)]:
            next_pos = (current[0] + dx, current[1] + dy)
            if next_pos[0] < 0 or next_pos[0] >= n_rows or next_pos[1] < 0 or next_pos[1] >= n_cols:
                continue
            if next_pos not in visited and map[next_pos[0]][next_pos[1]] == 0:
                visited.add(next_pos)
                d[next_pos] = d[current] + 1
                queue.append((next_pos, path + [next_pos]))

    if start not in d:
        return 'S', 100000

    t = 0
    actions = ['U', 'D', 'L', 'R']
    current = start
    for dx, dy in [(-1, 0), (1, 0), (0, -1), (0, 1)]:
        next_pos = (current[0] + dx, current[1] + dy)
        if next_pos in d:
            if d[next_pos] == d[current] - 1:
                return actions[t], d[next_pos]
        t += 1
    return 'S', d[start]


class GreedyAgents:

    def __init__(self):
        self.agents = []
        self.packages = []
        self.packages_free = []
        self.n_robots = 0
        self.state = None

        self.is_init = False

    def init_agents(self, state):
        self.state = state
        self.n_robots = len(state['robots'])
        self.map = state['map']
        self.robots = [(robot[0] - 1, robot[1] - 1, 0) for robot in state['robots']]
        self.robots_target = ['free'] * self.n_robots
        self.packages += [(p[0], p[1] - 1, p[2] - 1, p[3] - 1, p[4] - 1, p[5]) for p in state['packages']]

        self.packages_free = [True] * len(self.packages)

    def update_move_to_target(self, robot_id, target_package_id, phase='start'):

        if phase == 'start':
            distance = abs(self.packages[target_package_id][1] - self.robots[robot_id][0]) + \
                       abs(self.packages[target_package_id][2] - self.robots[robot_id][1])
        else:
            # Switch to the distance to target (3, 4) if phase == 'target'
            distance = abs(self.packages[target_package_id][3] - self.robots[robot_id][0]) + \
                       abs(self.packages[target_package_id][4] - self.robots[robot_id][1])
        i = robot_id
        # print(self.robots[i], distance, phase)

        # Step 4: Move to the package
        pkg_act = 0
        move = 'S'
        if distance >= 1:
            pkg = self.packages[target_package_id]

            target_p = (pkg[1], pkg[2])
            if phase == 'target':
                target_p = (pkg[3], pkg[4])
            move, distance = run_bfs(self.map, (self.robots[i][0], self.robots[i][1]), target_p)

            if distance == 0:
                if phase == 'start':
                    pkg_act = 1  # Pickup
                else:
                    pkg_act = 2  # Drop
        else:
            move = 'S'
            pkg_act = 1
            if phase == 'start':
                pkg_act = 1  # Pickup
            else:
                pkg_act = 2  # Drop

        return move, str(pkg_act)

    def update_inner_state(self, state):
        # Update robot positions and states
        for i in range(len(state['robots'])):
            prev = (self.robots[i][0], self.robots[i][1], self.robots[i][2])
            robot = state['robots'][i]
            self.robots[i] = (robot[0] - 1, robot[1] - 1, robot[2])
            # print(i, self.robots[i])
            if prev[2] != 0:
                if self.robots[i][2] == 0:
                    # Robot has dropped the package
                    self.robots_target[i] = 'free'
                else:
                    self.robots_target[i] = self.robots[i][2]

        # Update package positions and states
        self.packages += [(p[0], p[1] - 1, p[2] - 1, p[3] - 1, p[4] - 1, p[5]) for p in state['packages']]
        self.packages_free += [True] * len(state['packages'])

    def get_actions(self, state):
        if self.is_init == False:
            # This mean we have invoke the init agents, use the update_inner_state to update the state
            self.is_init = True
            self.update_inner_state(state)

        else:
            self.update_inner_state(state)

        actions = []
        print("State robot: ", self.robots)
        # Start assigning a greedy strategy
        for i in range(self.n_robots):
            # Step 1: Check if the robot is already assigned to a package
            if self.robots_target[i] != 'free':

                closest_package_id = self.robots_target[i]
                # Step 1b: Check if the robot has reached the package
                if self.robots[i][2] != 0:
                    # Move to the target points

                    move, action = self.update_move_to_target(i, closest_package_id - 1, 'target')
                    actions.append((move, str(action)))
                else:
                    # Step 1c: Continue to move to the package
                    move, action = self.update_move_to_target(i, closest_package_id - 1)
                    actions.append((move, str(action)))
            else:
                # Step 2: Find a package to pick up
                # Find the closest package
                closest_package_id = None
                closed_distance = 1000000
                for j in range(len(self.packages)):
                    if not self.packages_free[j]:
                        continue

                    pkg = self.packages[j]
                    d = abs(pkg[1] - self.robots[i][0]) + abs(pkg[2] - self.robots[i][1])
                    if d < closed_distance:
                        closed_distance = d
                        closest_package_id = pkg[0]

                if closest_package_id is not None:
                    self.packages_free[closest_package_id - 1] = False
                    self.robots_target[i] = closest_package_id
                    move, action = self.update_move_to_target(i, closest_package_id - 1)
                    actions.append((move, str(action)))
                else:
                    actions.append(('S', '0'))

        print("N robots = ", len(self.robots))
        print("Actions = ", actions)
        print(self.robots_target)
        return actions

# Agentversion1

In [6]:
class AgentsVersion1:
    def __init__(self):
        self.n_robots = 0
        self.state = None

        # add feature
        self.robots = []
        self.packages = []
        self.board_path = {}
        self.map = []

        self.waiting_packages = []
        self.in_transit_packages = []
        self.transited_packages = []
        self.transit_succes = 0


    def init_agents(self, state):
        self.state = state
        self.n_robots = len(state['robots'])
        self.map = state['map']
        self.board_path = get_shortest_path(state['map'])
        self.robots = [(robot[0], robot[1], 0) for robot in state['robots']]

    def differ_connected(self, start, target):
        return (start, target) not in self.board_path


    def get_action(self, start, target):
        if start == target:
            return ""
        return self.board_path[(start, target)]

    def get_actions(self, state):
        actions = []
        packages = state['packages']
        robots = state['robots']
        map = state['map']

        # Add the newly created packages into waiting_packages
        for package in packages:
            self.packages.append(package)
            self.waiting_packages.append(package)
        for i in range(len(robots)):
            self.robots[i] = robots[i]

        for i in range(len(robots)):
            # move = str(np.random.choice(list_actions))
            move = 'S'
            pkg_act = 0

            pos_robot_i, pos_robot_j, carrying = robots[i]
            pos_robot = (pos_robot_i, pos_robot_j)

            if carrying != 0: # If the robot is transporting a package
                for package in self.in_transit_packages.copy():
                    if package[0] == carrying:
                        target_package = (package[3], package[4])
                        # As only deliverable packages are selected during traversal, paths that do not exist are ignored
                        move_path = self.get_action(pos_robot, target_package)
                        move = 'S' if len(move_path) == 0 else move_path[0]
                        if len(move_path) != 1:
                            pkg_act = 0
                        else:
                            pkg_act = 2
                            self.transited_packages.append(package)
                            self.transit_succes += 1
                            self.in_transit_packages.remove(package)
                        break
            else: # The robot is on its way to find the package with the shortest delivery pat
                final_package = (1, 1)
                len_min_path = 10000
                if len(self.waiting_packages) == 0:
                    actions.append((str('S'), str(0)))
                    continue

                pos_pack = (1, 1)

                for package in self.waiting_packages:
                    start_package = (package[1], package[2])
                    target_package = (package[3], package[4])
                    if self.differ_connected(pos_robot, start_package):
                        continue
                    if self.differ_connected(start_package, target_package):
                        continue
                    start_path = self.get_action(pos_robot, start_package)
                    target_path = self.get_action(start_package, target_package)
                    len_path = len(start_path) + len(target_path)

                    if len_path < len_min_path:
                        len_min_path = len_path
                        pos_pack = start_package
                    # elif len_path == len_min_path:
                    #     package_id = min(package_id, package[0])

                if pos_pack == (1, 1):
                    actions.append((str('S'), str(0)))
                    continue

                package_id = 10000
                for package in self.waiting_packages.copy():
                    if pos_pack == (package[1], package[2]):
                        package_id = min(package_id, package[0])

                for package in self.waiting_packages.copy():
                    if package[0] == package_id:
                        pos_package = (package[1], package[2])
                        move_path = self.get_action(pos_robot, pos_package)
                        move = 'S' if len(move_path) == 0 else move_path[0]
                        if len(move_path) == 1:
                            pkg_act = 1
                            self.in_transit_packages.append(package)
                            self.waiting_packages.remove(package)
                        else:
                            pkg_act = 0
                        break

            actions.append((str(move), str(pkg_act)))


        # Handle if there is a cycle
        old_move = {}
        new_move = {}
        still_move = {}
        for i in range(len(actions)):
            pos_robot = (robots[i][0], robots[i][1])
            old_move[pos_robot] = i
            new_move[compute_valid_position(map, pos_robot, actions[i][0])] = i
            if pos_robot != compute_valid_position(map, pos_robot, actions[i][0]):
                still_move[pos_robot] = i
        for i in range(len(actions)):
            pos_robot = (robots[i][0], robots[i][1])
            next_post = compute_valid_position(map, pos_robot, actions[i][0])
            if pos_robot in new_move and next_post in old_move and pos_robot != next_post:

                for move in ['L', 'R', 'U', 'D']:
                    if move != actions[i][0] and int(actions[i][1]) == 0:
                        new_pos = compute_valid_position(map, (robots[i][0], robots[i][1]), move)
                        if new_pos not in old_move and valid_position(map, new_pos):
                            actions[i] = (move, actions[i][1])
                            # return actions

        # If a moving robot would collide with a stationary robot, force the stationary robot to move
        occupied = {}
        old_pos = {}

        for i in range(len(actions)):
            pos_robot = (robots[i][0], robots[i][1])
            old_pos[pos_robot] = i
            if actions[i][0] != 'S':
                occupied[compute_valid_position(map, (robots[i][0], robots[i][1]), actions[i][0])] = i
        for i in range(len(actions)):
            pos_robot = (robots[i][0], robots[i][1])
            if actions[i][0] == 'S' and actions[i][1] != '1':
                for move in ['L', 'R', 'U', 'D']:
                    new_pos_robot = compute_valid_position(map, pos_robot, move)
                    # if new_pos not in occupied and valid_position(map, new_pos):
                    if new_pos_robot not in old_pos and pos_robot in occupied and valid_position(map, new_pos_robot):
                        actions[i] = (move, actions[i][1])
                        occupied[new_pos_robot] = i
        return actions

# Agentversion2

In [7]:
class AgentsVersion2:
    def __init__(self):
        self.n_robots = 0
        self.state = None

        # add feature
        self.robots = []
        self.packages = []
        self.board_path = {}
        self.map = []

        self.waiting_packages = []
        self.in_transit_packages = []
        self.transited_packages = []
        self.transit_succes = 0


    def init_agents(self, state):
        self.state = state
        self.n_robots = len(state['robots'])
        self.map = state['map']
        self.board_path = get_shortest_path(state['map'])
        self.robots = [(robot[0], robot[1], 0) for robot in state['robots']]

    def differ_connected(self, start, target):
        return (start, target) not in self.board_path


    def get_action(self, start, target):
        if start == target:
            return ""
        return self.board_path[(start, target)]
    def get_actions(self, state):
        actions = []
        packages = state['packages']
        robots = state['robots']
        map = state['map']

        # Add the newly created packages into waiting_packages
        for package in packages:
            self.packages.append(package)
            self.waiting_packages.append(package)
        for i in range(len(robots)):
            self.robots[i] = robots[i]

        for i in range(len(robots)):
            move = 'S'
            pkg_act = 0

            pos_robot_i, pos_robot_j, carrying = robots[i]
            pos_robot = (pos_robot_i, pos_robot_j)

            if carrying != 0: # If the robot is transporting a package
                for package in self.in_transit_packages.copy():
                    if package[0] == carrying:
                        target_package = (package[3], package[4])
                        # As only deliverable packages are selected during traversal, paths that do not exist are ignored
                        move_path = self.get_action(pos_robot, target_package)
                        move = 'S' if len(move_path) == 0 else move_path[0]
                        if len(move_path) > 1:
                            pkg_act = 0
                        else:
                            pkg_act = 2
                            self.transited_packages.append(package)
                            self.transit_succes += 1
                            self.in_transit_packages.remove(package)
                        break
            else: # The robot is on its way to find the package with the shortest delivery pat
                final_package = (1, 1)
                len_min_path = 10000
                if len(self.waiting_packages) == 0:
                    actions.append((str('S'), str(0)))
                    continue

                pos_pack = (1, 1)

                for package in self.waiting_packages:
                    start_package = (package[1], package[2])
                    target_package = (package[3], package[4])
                    if self.differ_connected(pos_robot, start_package):
                        continue
                    if self.differ_connected(start_package, target_package):
                        continue
                    start_path = self.get_action(pos_robot, start_package)
                    target_path = self.get_action(start_package, target_package)
                    len_path = len(start_path) + len(target_path)
                    # len_path = len(start_path)

                    if len_path <= len_min_path:
                        len_min_path = len_path
                        pos_pack = start_package
                    # elif len_path == len_min_path:
                    #     package_id = min(package_id, package[0])

                if pos_pack == (1, 1):
                    actions.append((str('S'), str(0)))
                    continue

                package_id = 10000
                for package in self.waiting_packages.copy():
                    if pos_pack == (package[1], package[2]):
                        package_id = min(package_id, package[0])

                for package in self.waiting_packages.copy():
                    if package[0] == package_id:
                        pos_package = (package[1], package[2])
                        move_path = self.get_action(pos_robot, pos_package)
                        move = 'S' if len(move_path) == 0 else move_path[0]
                        if len(move_path) <= 1:
                            pkg_act = 1
                            self.in_transit_packages.append(package)
                            self.waiting_packages.remove(package)
                        else:
                            pkg_act = 0
                        break

            actions.append((str(move), str(pkg_act)))

        # find all cycle in move actions
        cycles_list, actions_list = find_all_cycle(map, robots, actions)
        old_pos = {}
        new_pos = {}
        for i in range(len(actions)):
            pos_robot = (robots[i][0], robots[i][1])
            old_pos[pos_robot] = i
            new_pos[compute_valid_position(map, pos_robot, actions[i][0])] = i

        for (element_robot, element_action) in zip(cycles_list, actions_list):
            # Handle if there is multi cycle
            for i in range(len(element_action)):
                pos_robot = (element_robot[i][0], element_robot[i][1])
                next_pos = compute_valid_position(map, pos_robot, element_action[i][0])
                if pos_robot in new_pos and next_pos in old_pos and pos_robot != next_pos:
                    moves = ['L', 'R', 'U', 'D']
                    moves.remove(element_action[i][0])
                    # random.shuffle(moves)
                    # for move in ['L', 'R', 'U', 'D']:
                    for move in moves:
                        # print(i, move, actions[i][0], actions[i][1], type( actions[i][0]), type( actions[i][1]))
                        # if move != element_action[i][0] and int(element_action[i][1]) == 0:
                        if move != element_action[i][0]:
                            new_pos_robot = compute_valid_position(map, pos_robot, move)
                            if new_pos_robot not in old_pos and new_pos_robot not in new_pos and valid_position(map, new_pos_robot):
                                new_pos[new_pos_robot] = i
                                element_action[i] = (move, element_action[i][1])
                                # return actions
                for j in range(len(robots)):
                    if pos_robot == (robots[j][0], robots[j][1]):
                        actions[j] = element_action[i]

        # If a moving robot would collide with a stationary robot, force the stationary robot to move
        for i in range(len(actions)):
            pos_robot = (robots[i][0], robots[i][1])
            if actions[i][0] == 'S' and actions[i][1] != '1':
                for move in ['L', 'R', 'U', 'D']:
                    new_pos_robot = compute_valid_position(map, pos_robot, move)
                    # if new_pos not in occupied and valid_position(map, new_pos):
                    if new_pos_robot not in old_pos and new_pos_robot not in new_pos and pos_robot in new_pos and valid_position(map, new_pos_robot):
                        actions[i] = (move, actions[i][1])
                        new_pos[new_pos_robot] = i
                        # break
        return actions

# Agentversion3

In [8]:
class AgentsVersion3:
    def __init__(self):
        self.n_robots = 0
        self.state = None

        # add feature
        self.robots = []
        self.packages = []
        self.board_path = {}
        self.map = []

        self.waiting_packages = []
        self.in_transit_packages = []
        self.transited_packages = []
        self.transit_succes = 0


    def init_agents(self, state):
        self.state = state
        self.n_robots = len(state['robots'])
        self.map = state['map']
        self.board_path = get_shortest_path(state['map'])
        self.robots = [(robot[0], robot[1], 0) for robot in state['robots']]

    def differ_connected(self, start, target):
        return (start, target) not in self.board_path


    def get_action(self, start, target):
        if start == target:
            return ""
        return self.board_path[(start, target)]

    def get_actions(self, state):
        actions = []
        packages = state['packages']
        robots = state['robots']
        map = state['map']

        # Add the newly created packages into waiting_packages
        for package in packages:
            self.packages.append(package)
            self.waiting_packages.append(package)

        for i in range(len(robots)):
            # move = str(np.random.choice(list_actions))
            move = 'S'
            pkg_act = 0

            last_pos_robot_i, last_pos_robot_j, last_carrying = self.robots[i]
            last_pos_robot = (last_pos_robot_i, last_pos_robot_j)

            pos_robot_i, pos_robot_j, carrying = robots[i]
            pos_robot = (pos_robot_i, pos_robot_j)

            if carrying != 0: # If the robot is transporting a package
                if last_carrying == 0:
                    for package in self.waiting_packages.copy():
                        if package[0] == carrying:
                            self.in_transit_packages.append(package)
                            self.waiting_packages.remove(package)
                            break

                for package in self.in_transit_packages:
                    if package[0] == carrying:
                        target_package = (package[3], package[4])
                        # As only deliverable packages are selected during traversal, paths that do not exist are ignored
                        move_path = self.get_action(pos_robot, target_package)
                        move = 'S' if len(move_path) == 0 else move_path[0]
                        pkg_act = 2 if len(move_path) <= 1 else 0
                        break

            else: # The robot is on its way to find the package with the shortest delivery pat
                if last_carrying != 0:
                    for package in self.in_transit_packages.copy():
                        if package[0] == last_carrying:
                            self.transited_packages.append(package)
                            self.transit_succes += 1
                            self.in_transit_packages.remove(package)
                            break

                len_min_path = 10000
                if len(self.waiting_packages) == 0:
                    actions.append((str('S'), str(0)))
                    continue

                pos_pack = (1, 1)

                for package in self.waiting_packages:
                    start_package = (package[1], package[2])
                    target_package = (package[3], package[4])
                    if self.differ_connected(pos_robot, start_package):
                        continue
                    if self.differ_connected(start_package, target_package):
                        continue
                    start_path = self.get_action(pos_robot, start_package)
                    target_path = self.get_action(start_package, target_package)
                    len_path = (4 * len(start_path) + 2 * len(target_path))

                    if len_path <= len_min_path:
                        len_min_path = len_path
                        pos_pack = start_package
                    # elif len_path == len_min_path:
                    #     package_id = min(package_id, package[0])

                if pos_pack == (1, 1):
                    actions.append((str('S'), str(0)))
                    continue

                package_id = 10000
                for package in self.waiting_packages.copy():
                    if pos_pack == (package[1], package[2]):
                        package_id = min(package_id, package[0])

                for package in self.waiting_packages:
                    if package[0] == package_id:
                        pos_package = (package[1], package[2])
                        if self.differ_connected(pos_robot, pos_package):
                            continue
                        move_path = self.get_action(pos_robot, pos_package)
                        move = 'S' if len(move_path) == 0 else move_path[0]
                        pkg_act = 1 if len(move_path) <= 1 else 0
                        break

            actions.append((str(move), str(pkg_act)))

        # update position robot into Agents
        for i in range(len(robots)):
            self.robots[i] = robots[i]

        # find all cycle in move actions
        # print(len(robots), len(actions), robots, actions)
        cycles_list, actions_list = find_all_cycle(map, robots, actions)
        old_pos = {}
        new_pos = {}
        for i in range(len(actions)):
            pos_robot = (robots[i][0], robots[i][1])
            old_pos[pos_robot] = i
            new_pos[compute_valid_position(map, pos_robot, actions[i][0])] = i

        for (element_robot, element_action) in zip(cycles_list, actions_list):
            # Handle if there is multi cycle
            check = False
            for i in range(len(element_action)):
                pos_robot = (element_robot[i][0], element_robot[i][1])
                next_pos = compute_valid_position(map, pos_robot, element_action[i][0])
                if pos_robot in new_pos and next_pos in old_pos and pos_robot != next_pos:
                    moves = ['L', 'R', 'U', 'D']
                    moves.remove(element_action[i][0])
                    random.shuffle(moves)
                    # for move in ['L', 'R', 'U', 'D']:
                    for move in moves:
                        if move != element_action[i][0]:
                            new_pos_robot = compute_valid_position(map, pos_robot, move)
                            if new_pos_robot not in old_pos and new_pos_robot not in new_pos and valid_position(map, new_pos_robot):

                                new_pos[new_pos_robot] = i
                                element_action[i] = (move, element_action[i][1])
                                check = True
                                break
                # if check:
                #     break
                for j in range(len(robots)):
                    if pos_robot == (robots[j][0], robots[j][1]):
                        actions[j] = element_action[i]
        # If a moving robot would collide with a stationary robot, force the stationary robot to move
        for i in range(len(actions)):
            pos_robot = (robots[i][0], robots[i][1])
            if actions[i][0] == 'S' and actions[i][1] != '1':
                moves = ['L', 'R', 'U', 'D']
                random.shuffle(moves)
                for move in moves:
                    new_pos_robot = compute_valid_position(map, pos_robot, move)
                    # if new_pos not in occupied and valid_position(map, new_pos):
                    if new_pos_robot not in old_pos and new_pos_robot not in new_pos and pos_robot in new_pos and valid_position(map, new_pos_robot):
                        actions[i] = (move, actions[i][1])
                        new_pos[new_pos_robot] = i
                        break
        cycle_list, action_list = find_all_cycle(map, robots, actions)
        return actions

# Agentversion4

In [9]:
class AgentsVersion4:
    def __init__(self):
        self.n_robots = 0
        self.state = None

        # add feature
        self.robots = []
        self.packages = []
        self.board_path = {}
        self.map = []

        self.waiting_packages = []
        self.in_transit_packages = []
        self.transited_packages = []
        self.transit_succes = 0


    def init_agents(self, state):
        self.state = state
        self.n_robots = len(state['robots'])
        self.map = state['map']
        self.board_path = get_shortest_path(state['map'])
        self.robots = [(robot[0], robot[1], 0) for robot in state['robots']]

    def differ_connected(self, start, target):
        return (start, target) not in self.board_path


    def get_action(self, start, target):
        if start == target:
            return ""
        return self.board_path[(start, target)]

    def get_actions(self, state):
        actions = []
        packages = state['packages']
        robots = state['robots']
        map = state['map']

        packages_owned = []

        # Add the newly created packages into waiting_packages
        for package in packages:
            self.packages.append(package)
            self.waiting_packages.append(package)

        for i in range(len(robots)):
            # move = str(np.random.choice(list_actions))
            move = 'S'
            pkg_act = 0

            last_pos_robot_i, last_pos_robot_j, last_carrying = self.robots[i]

            pos_robot_i, pos_robot_j, carrying = robots[i]
            pos_robot = (pos_robot_i, pos_robot_j)

            if carrying != 0: # If the robot is transporting a package
                if last_carrying == 0:
                    for package in self.waiting_packages.copy():
                        if package[0] == carrying:
                            self.in_transit_packages.append(package)
                            self.waiting_packages.remove(package)
                            break

                for package in self.in_transit_packages:
                    if package[0] == carrying:
                        target_package = (package[3], package[4])
                        # As only deliverable packages are selected during traversal, paths that do not exist are ignored
                        move_path = self.get_action(pos_robot, target_package)
                        move = 'S' if len(move_path) == 0 else move_path[0]
                        pkg_act = 2 if len(move_path) <= 1 else 0
                        break

            else: # The robot is on its way to find the package with the shortest delivery pat
                if last_carrying != 0:
                    for package in self.in_transit_packages.copy():
                        if package[0] == last_carrying:
                            self.transited_packages.append(package)
                            self.transit_succes += 1
                            self.in_transit_packages.remove(package)
                            break

                len_min_path = 10000
                if len(self.waiting_packages) == 0:
                    actions.append((str('S'), str(0)))
                    continue

                pos_pack = (1, 1)

                for package in self.waiting_packages:
                    if package[0] not in packages_owned:
                    # if True:
                        start_package = (package[1], package[2])
                        target_package = (package[3], package[4])
                        if self.differ_connected(pos_robot, start_package):
                            continue
                        if self.differ_connected(start_package, target_package):
                            continue
                        start_path = self.get_action(pos_robot, start_package)
                        target_path = self.get_action(start_package, target_package)
                        len_path = (4 * len(start_path) + 2 * len(target_path))

                        if len_path <= len_min_path:
                            len_min_path = len_path
                            pos_pack = start_package
                    # elif len_path == len_min_path:
                    #     package_id = min(package_id, package[0])

                if pos_pack == (1, 1):
                    actions.append((str('S'), str(0)))
                    continue

                package_id = 10000
                for package in self.waiting_packages.copy():
                    if pos_pack == (package[1], package[2]):
                        package_id = min(package_id, package[0])

                for package in self.waiting_packages:
                    if package[0] == package_id:
                        packages_owned.append(package[0])
                        pos_package = (package[1], package[2])
                        move_path = self.get_action(pos_robot, pos_package)
                        move = 'S' if len(move_path) == 0 else move_path[0]
                        pkg_act = 1 if len(move_path) <= 1 else 0
                        break

            actions.append((str(move), str(pkg_act)))

        # update position robot into Agents
        for i in range(len(robots)):
            self.robots[i] = robots[i]

        # find all cycle in move actions
        # print(len(robots), len(actions), robots, actions)
        cycles_list, actions_list = find_all_cycle(map, robots, actions)
        old_pos = {}
        new_pos = {}
        for i in range(len(actions)):
            pos_robot = (robots[i][0], robots[i][1])
            old_pos[pos_robot] = i
            new_pos_robot = compute_valid_position(map, pos_robot, actions[i][0])
            if new_pos_robot not in new_pos:
                new_pos[new_pos_robot] = []
            new_pos[new_pos_robot].append(i)

        for (element_robot, element_action) in zip(cycles_list, actions_list):
            # Handle if there is multi cycle
            check = False
            for i in range(len(element_action)):
                pos_robot = (element_robot[i][0], element_robot[i][1])
                next_pos = compute_valid_position(map, pos_robot, element_action[i][0])
                if pos_robot in new_pos and next_pos in old_pos and pos_robot != next_pos:
                    moves = ['L', 'R', 'U', 'D']
                    moves.remove(element_action[i][0])
                    random.shuffle(moves)
                    # for move in ['L', 'R', 'U', 'D']:
                    for move in moves:
                        if move != element_action[i][0]:
                            new_pos_robot = compute_valid_position(map, pos_robot, move)
                            if new_pos_robot not in old_pos and new_pos_robot not in new_pos and valid_position(map, new_pos_robot):
                                new_pos[new_pos_robot] = []
                                new_pos[new_pos_robot].append(i)

                                element_action[i] = (move, element_action[i][1])
                                check = True
                                break
                for j in range(len(robots)):
                    if pos_robot == (robots[j][0], robots[j][1]):
                        actions[j] = element_action[i]
                if check:
                    break

        # If a moving robot would collide with a stationary robot, force the stationary robot to move
        for i in range(len(actions)):
            pos_robot = (robots[i][0], robots[i][1])
            if actions[i][0] == 'S' and actions[i][1] != '1':
                if pos_robot in new_pos and len(new_pos[pos_robot]) == 1:
                    continue
                moves = ['L', 'R', 'U', 'D']
                random.shuffle(moves)
                for move in moves:
                    new_pos_robot = compute_valid_position(map, pos_robot, move)
                    # if new_pos not in occupied and valid_position(map, new_pos):
                    if new_pos_robot not in old_pos and new_pos_robot not in new_pos and pos_robot in new_pos and valid_position(map, new_pos_robot):
                        actions[i] = (move, actions[i][1])
                        new_pos[new_pos_robot] = []
                        new_pos[new_pos_robot].append(i)
                        break
        cycle_list, action_list = find_all_cycle(map, robots, actions)
        return actions

# Agentversion5

In [10]:
class AgentsVersion5:
    # Khởi tạo mặc định
    def __init__(self):
        self.state = None
        self.map = []
        self.board_path = {} # Ánh xạ (start_pos, target_pos) với đường đi giữa 2 v trí
        self.robots = [] # Lưu thông tin của các robot (trước khi nhận state mới)
        self.packages = {} # Lưu tất cả packages đã xuất hiện (dùng map để dễ truy cập thông qua id mà không cần quan tâm thứ tự trong mảng)
        self.waiting_packages = [] # Danh sách gói hàng trong trạng thái chờ
        self.transiting_packages = [] # Danh sách gói hàng đang được giao
        self.transited_packages = [] # Danh sách gói hàng đã được giao
        self.target_transit = {} # Ánh xạ robot với waiting package đang được chỉ định phải nhặt
        self.count_repeat = [] # Lưu số lần vị trí đã được lặp lại
        self.last_move = [] # Lưu move của step trước

        self.NUM_REPEAT = 2 # Số lần vị trí lặp lại cần để thực hiện random

    # Khởi tạo thông tin dựa trên state được khởi tạo ban đầu
    def init_agents(self, state):
        self.state = state
        self.map = state['map']
        self.board_path = get_shortest_path(state['map'])
        self.robots = [(robot[0], robot[1], 0) for robot in state['robots']]
        self.count_repeat = [0] * len(state['robots'])

    # Kiểm tra 2 vị trí có cùng thành phần liên thông không
    def differ_connected(self, start, target):
        return (start, target) not in self.board_path

    # Lấy str biểu diễn đường đi từ start tới target (khác hoàn toàn target tơi start)
    def get_action(self, start, target):
        # Nếu 2 vị trí trùng nhau tức là không cần di chuyển
        if start == target:
            return ""
        return self.board_path[(start, target)]

    # Đưa ra action cho từng robot theo thứ tự dựa trên state nhận được
    def get_actions(self, state, alpha=1, beta=1):
        actions = []
        map = state['map']
        robots = state['robots']
        packages = state['packages']

        packages_owned = []

        # Thêm tất cả package mới xuất hiện vào danh sách chờ
        for package in packages:
            self.packages[package[0]] = package
            self.waiting_packages.append(package)

        # Duyệt qua từng robot
        for i in range(len(robots)):
            # Nếu vị trí lặp lại quá nhiều lần thì sẽ xử lý bằng cách random hướng để thoát khỏi thế đứng im đó
            if (robots[i][0], robots[i][1]) == (self.robots[i][0], self.robots[i][1]):
                self.count_repeat[i] += 1
            else:
                self.count_repeat[i] = 1
            if self.count_repeat[i] >= self.NUM_REPEAT and self.last_move[i][0] != 'S' and self.last_move[i][1] != '1':
                moves = ['L', 'R', 'U', 'D']
                moves.remove(self.last_move[i][0])
                move_action = random.choice(moves)
                actions.append((str(move_action), str(0)))
                continue

            last_pos_robot_i, last_pos_robot_j, last_carrying = self.robots[i]
            pos_robot_i, pos_robot_j, carrying = robots[i]
            pos_robot = (pos_robot_i, pos_robot_j)

            if carrying != 0: # Nếu robot đang cầm package
                # Robot vừa nhặt thành công package trong step trước
                if last_carrying == 0:
                    self.transiting_packages.append(self.packages[carrying])
                    self.waiting_packages.remove(self.packages[carrying])

                # Robot đang trên đường đi giao package

                transiting_package = self.packages[carrying] # Gói hàng đang được giao (truy xuất thông qua carrying)
                target_pos = (transiting_package[3], transiting_package[4])
                # Vì lúc nhặt đã xét chỉ nhặt gói hàng có start và target trong 1 thành phần liên thông, nên luôn tồn tại đường đi rồi
                move_path = self.get_action(pos_robot, target_pos)
                move = 'S' if len(move_path) == 0 else move_path[0]
                pkg_act = 2 if len(move_path) <= 1 else 0
                actions.append((str(move), str(pkg_act)))
                continue
            else: # Nếu robot đang không cầm package nào
                # Robot mới thả package trong step trước
                if last_carrying != 0:
                    transited_package = self.packages[last_carrying]
                    self.transited_packages.append(transited_package)
                    self.transiting_packages.remove(transited_package)

                # Tìm đường đi nhặt gói hàng có tổng quãng đường gần nhất
                # Nếu đang hết package chờ được giao thì cho robot stay
                if len(self.waiting_packages) == 0:
                    actions.append((str('S'), str(0)))
                    continue

                # Ánh xạ từ vị trí chứa package tới tập các package_id trong vị trí đó
                valid_pos_package = {}
                for package in self.waiting_packages:
                    pos = (package[1], package[2])
                    # Bỏ qua những package_id đã được nhắm để nhặt
                    if pos in packages_owned:
                        continue
                    # Nếu chưa tồn tại vị trí trong map thì gán giá trị bằng package_id luôn
                    if pos not in valid_pos_package:
                        valid_pos_package[pos] = package[0]
                    # Nếu đã tồn tại thì gán với package_id nhỏ nhất
                    valid_pos_package[pos] = min(valid_pos_package[pos], package[0])

                len_min_path = 10000
                package_id = -1

                # Tìm package tốt nhất
                for start_package in valid_pos_package:
                    package = self.packages[valid_pos_package[start_package]]
                    # if package[0] in packages_owned # Dùng để tránh 2 robot cùng đi nhặt 1 package
                    if True:
                        target_package = (package[3], package[4])

                        # Nếu (pos_package và start_package) hoặc (start_package) khác thành phần liên thông thì bỏ qua không nhặt
                        # (Vì nếu không sẽ lỗi truy xuất đường đi)
                        if self.differ_connected(pos_robot, start_package):
                            continue
                        if self.differ_connected(start_package, target_package):
                            continue

                        # Hàm đánh giá lựa chọn là tổng quãng đường từ vị trí hiện tại với vị trí package và tới vị trí giao package
                        start_path = self.get_action(pos_robot, start_package)
                        target_path = self.get_action(start_package, target_package)
                        len_path = alpha * len(start_path) + beta * len(target_path)

                        if state['time_step'] + len_path > package[6]:
                            continue
                        if len_path < len_min_path:
                            len_min_path = len_path
                            package_id = package[0]

                # Không tìm thấy package nào phù hợp để nhặt
                if package_id == -1:
                    actions.append((str('S'), str(0)))
                    continue

                # Vì nếu có package_id thỏa mãn thì robot chắc chắn nhặt được (mà đảm bảo không nhặt cùng robot khác)
                waited_package = self.packages[package_id]

                start_package = (waited_package[1], waited_package[2])
                packages_owned.append(start_package)

                move_path = self.get_action(pos_robot, start_package)
                move = 'S' if len(move_path) == 0 else move_path[0]
                pkg_act = 1 if len(move_path) <= 1 else 0
                actions.append((str(move), str(pkg_act)))

        # Cập nhật vị trí robot của state hiện tại vào bộ nhớ
        for i in range(len(robots)):
            self.robots[i] = robots[i]

        old_pos = {} # Ánh xạ vị trí có robot đang đứng đến id của robot đó
        new_pos = {} # Ánh xạ từ 1 vị trí đến danh sách id các robot muốn tới vị trí đó

        # Lưu thông tin về robot hiện tại và dự định
        for i in range(len(actions)):
            pos_robot = (robots[i][0], robots[i][1])
            old_pos[pos_robot] = i
            next_pos_robot = compute_valid_position(map, pos_robot, actions[i][0])

            # Kiểm tra vị trí muốn tới có trong danh sách chưa, nếu chưa thì tạo 1 mảng để lưu các id robot
            if next_pos_robot not in new_pos:
                new_pos[next_pos_robot] = []
            new_pos[next_pos_robot].append(pos_robot)

        # Tìm tất cả chu trình sẽ xảy ra
        cycles_list, actions_list = find_all_cycle(map, robots, actions)

        # Duyệt qua từng chu trình để phá trạng thái này
        for (element_robot, element_action) in zip(cycles_list, actions_list):
            check = False # Biến kiểm tra xem có phá trạng thái chu trình bằng cách thay đổi action của 1 robot chưa
            for i in range(len(element_action)):
                pos_robot = (element_robot[i][0], element_robot[i][1])
                next_pos_robot = compute_valid_position(map, pos_robot, element_action[i][0])

                # Vì nó là chu trình, nên không cần xét vị trí mới có thuộc các tập không (chắc chắn phải thuộc tập hợp)
                moves = ['L', 'R', 'U', 'D']
                moves.remove(element_action[i][0])
                # random.shuffle(moves) # Có thể dùng

                # Duyệt từng hướng di chuyển xem có thay đổi được action đang xét không
                for move in moves:
                    new_pos_robot = compute_valid_position(map, pos_robot, move)
                    if new_pos_robot not in old_pos and new_pos_robot not in new_pos:
                        new_pos[new_pos_robot] = [pos_robot] # Có thể gán bằng bất cứ số nào, chỉ ần để new_pos_robot có trong new_pos
                        new_pos[next_pos_robot].remove(pos_robot)
                        check = True

                        for j in range(len(robots)):
                            if pos_robot == (robots[j][0], robots[j][1]):
                                actions[j] = (move, element_action[i][1])
                        break

                # Nếu đã thay đổi thành công 1 action trong cycle thì thoát khỏi cycle luôn (tránh thay đổi tất cả action thì vô nghĩa)
                if check:
                    break

        # Xử lý những robot có thể gây chắn đường khi ở trạng thái
        for i in range(len(actions)):
            pos_robot = (robots[i][0], robots[i][1])
            if actions[i][0] == 'S' and actions[i][1] != '1':
                if len(new_pos[pos_robot]) > 1: # Có robot khác muốn đi tới vị trí này
                    moves = ['L', 'R', 'U', 'D']
                    # random.shuffle(moves)

                    # Duyệt từng hướng di chuyển xem có thay đổi được action đang xét không
                    for move in moves:
                        new_pos_robot = compute_valid_position(map, pos_robot, move)
                        if new_pos_robot not in old_pos and new_pos_robot not in new_pos:
                            actions[i] = (move, actions[i][1])
                            new_pos[new_pos_robot] = [pos_robot]
                            break

        self.last_move = actions
        return actions

# AgentVersion6

In [11]:
class AgentsVersion6:
    # Khởi tạo mặc định
    def __init__(self):
        self.state = None
        self.map = []
        self.board_path = {} # Ánh xạ (start_pos, target_pos) với đường đi giữa 2 v trí
        self.robots = [] # Lưu thông tin của các robot (trước khi nhận state mới)
        self.packages = {} # Lưu tất cả packages đã xuất hiện (dùng map để dễ truy cập thông qua id mà không cần quan tâm thứ tự trong mảng)
        self.waiting_packages = [] # Danh sách gói hàng trong trạng thái chờ
        self.transiting_packages = [] # Danh sách gói hàng đang được giao
        self.transited_packages = [] # Danh sách gói hàng đã được giao
        self.target_transit = {} # Ánh xạ robot với waiting package đang được chỉ định phải nhặt
        self.count_repeat = [] # Lưu số lần vị trí đã được lặp lại
        self.last_move = [] # Lưu move của step trước

        self.NUM_REPEAT = 5 # Số lần vị trí lặp lại cần để thực hiện random

    # Khởi tạo thông tin dựa trên state được khởi tạo ban đầu
    def init_agents(self, state):
        self.state = state
        self.map = state['map']
        self.board_path = get_shortest_path(state['map'])
        self.robots = [(robot[0], robot[1], 0) for robot in state['robots']]
        self.count_repeat = [0] * len(state['robots'])

    # Kiểm tra 2 vị trí có cùng thành phần liên thông không
    def differ_connected(self, start, target):
        return (start, target) not in self.board_path

    # Lấy str biểu diễn đường đi từ start tới target (khác hoàn toàn target tơi start)
    def get_action(self, start, target):
        # Nếu 2 vị trí trùng nhau tức là không cần di chuyển
        if start == target:
            return ""
        return self.board_path[(start, target)]

    # Dùng luồng để tìm tìm tổng đường đi ngắn nhất cho tất cả robot / tất cả gói hàng hiện có
    def optimal_assign(self, now_step, robots, packages, alpha=1, beta=1):
        # robots gồm các phần tử dạng (robot_id, robot_x, robot_y)
        # packages gồm các package theo cấu trúc đã cho
        G = nx.DiGraph()
        G.add_node('s')
        G.add_node('t')

        # 1) s → robot
        for robot in robots:
            robot_id = robot[0]
            G.add_edge('s', f"robot_{robot_id}", capacity=1, weight=0)

        # 2) robot → package
        for robot in robots:
            robot_id = robot[0]
            for package in packages:
                package_id = package[0]
                pos_robot = (robot[1], robot[2])
                start_package = (package[1], package[2])
                target_package = (package[3], package[4])


                len_path = alpha * len(self.get_action(pos_robot, start_package)) + beta * len(self.get_action(start_package, target_package))
                if now_step + len_path > package[6]:
                    continue
                G.add_edge(f"robot_{robot_id}", f"package_{package_id}", capacity=1, weight=len_path)

        # 3) package → t
        for package in packages:
            package_id = package[0]
            G.add_edge(f"package_{package_id}", 't', capacity=1, weight=0)

        flow_dict = nx.max_flow_min_cost(G, 's', 't')

        list_package = []
        list_robot = []
        result = {}
        for u, flows in flow_dict.items():
            # Bỏ qua các node không phải là robot
            # -> chỉ quan tâm cạnh nối từ robot->package
            if not u.startswith('robot'):
                continue

            robot_id = int(u.split('_')[1])
            for v, f in flows.items():
                if f>0 and v.startswith('package'):
                    package_id = int(v.split('_')[1])
                    result[robot_id] = package_id
                    list_package.append(package_id)
                    list_robot.append(robot_id)

        # Nếu có robot chưa được gán với package nào (vì chê khi nhặt thì giao đã quá hạn)
        for robot in robots:
            robot_id = robot[0]
            if robot_id in list_robot:
                continue
            for package in packages:
                package_id = package[0]
                if package_id in list_package:
                    continue
                pos_robot = (robot[1], robot[2])
                start_package = (package[1], package[2])
                target_package = (package[3], package[4])

                len_path = alpha * len(self.get_action(pos_robot, start_package)) + beta * len(self.get_action(start_package, target_package))
                G.add_edge(f"robot_{robot_id}", f"package_{package_id}", capacity=1, weight=len_path)

        result = {}
        for u, flows in flow_dict.items():
            # Bỏ qua các node không phải là robot
            # -> chỉ quan tâm cạnh nối từ robot->package
            if not u.startswith('robot'):
                continue

            robot_id = int(u.split('_')[1])
            for v, f in flows.items():
                if f > 0 and v.startswith('package'):
                    package_id = int(v.split('_')[1])
                    result[robot_id] = package_id
                    list_package.append(package_id)
                    list_robot.append(robot_id)

        return result

    # Đưa ra action cho từng robot theo thứ tự dựa trên state nhận được
    def get_actions(self, state):
        # print(state)

        actions = []
        map = state['map']
        robots = state['robots']
        packages = state['packages']

        # Thêm tất cả package mới xuất hiện vào danh sách chờ
        for package in packages:
            self.packages[package[0]] = package
            self.waiting_packages.append(package)

        compute_robots = []
        compute_packages = []

        # Duyệt qua từng robot (chỉ duyệt robot đang giao hàng)
        for i in range(len(robots)):
            # Nếu vị trí lặp lại quá nhiều lần thì sẽ xử lý bằng cách random hướng để thoát khỏi thế đứng im đó
            if (robots[i][0], robots[i][1]) == (self.robots[i][0], self.robots[i][1]):
                self.count_repeat[i] += 1
            else:
                self.count_repeat[i] = 1
            if self.count_repeat[i] >= self.NUM_REPEAT and self.last_move[i][0] != 'S' and self.last_move[i][1] != '1':
                pos_robot = (robots[i][0], robots[i][1])
                moves = ['L', 'R', 'U', 'D']
                moves.remove(self.last_move[i][0])
                move_action = random.choice(moves)
                new_pos_robot = compute_valid_position(map, pos_robot, move_action)
                if new_pos_robot == pos_robot:
                    move_action = 'S'
                actions.append((str(move_action), str(0)))
                continue

            last_pos_robot_i, last_pos_robot_j, last_carrying = self.robots[i]
            pos_robot_i, pos_robot_j, carrying = robots[i]
            pos_robot = (pos_robot_i, pos_robot_j)
            # print(f"Robot {i} dang o vi tri {pos_robot}")

            if carrying != 0: # Nếu robot đang cầm package
                # Robot vừa nhặt thành công package trong step trước
                if last_carrying == 0:
                    self.transiting_packages.append(self.packages[carrying])
                    self.waiting_packages.remove(self.packages[carrying])

                # Robot đang trên đường đi giao package
                # print(f"Transit package set includes: {self.transiting_packages}")
                # print(f"Robot {i} in {pos_robot} and carry package_id {carrying}")

                transiting_package = self.packages[carrying] # Gói hàng đang được giao (truy xuất thông qua carrying)
                target_pos = (transiting_package[3], transiting_package[4])
                # print(f"Target package {carrying} in {target_pos}")
                # Vì lúc nhặt đã xét chỉ nhặt gói hàng có start và target trong 1 thành phần liên thông, nên luôn tồn tại đường đi rồi
                move_path = self.get_action(pos_robot, target_pos)
                move = 'S' if len(move_path) == 0 else move_path[0]
                pkg_act = 2 if len(move_path) <= 1 else 0
                actions.append((str(move), str(pkg_act)))
                continue
            else: # Nếu robot đang không cầm package nào
                # Robot mới thả package trong step trước
                if last_carrying != 0:
                    transited_package = self.packages[last_carrying]
                    self.transited_packages.append(transited_package)
                    self.transiting_packages.remove(transited_package)

                # Tìm đường đi nhặt gói hàng có tổng quãng đường gần nhất
                # Nếu đang hết package chờ được giao thì cho robot stay
                if len(self.waiting_packages) == 0:
                    actions.append((str('S'), str(0)))
                    continue

                # Thêm vào danh sách những robot đang tìm đường nhặt package
                compute_robots.append((i, robots[i][0], robots[i][1]))
                actions.append((str('S'), str(0))) # Gán để lấp đầy actions, sau có thể dễ dàng thay đổi giá trị thông qua robot_id tương ứng

        # print(f"Waiting package set includes: {self.waiting_packages}")

        # Ánh xạ từ vị trí chứa package tới tập các package_id sẽ nhận trong vị trí đó (là package_id bé nhất trong đó)
        valid_pos_package = {}
        for package in self.waiting_packages:
            pos = (package[1], package[2])

            # Nếu chưa tồn tại vị trí trong map thì gán giá trị bằng package_id luôn
            if pos not in valid_pos_package:
                valid_pos_package[pos] = package[0]
            # Nếu đã tồn tại thì gán với package_id nhỏ nhất
            valid_pos_package[pos] = min(valid_pos_package[pos], package[0])

        values_package = valid_pos_package.values()
        for package_id in values_package:
            package = self.packages[package_id]
            compute_packages.append(package)

        # print(compute_robots, compute_packages)
        optimal_assign = self.optimal_assign(state['time_step'], compute_robots, compute_packages)
        # print(f"Optimal assign: {optimal_assign}")
        for robot_id, package_id in optimal_assign.items():
            pos_robot = (robots[robot_id][0], robots[robot_id][1])
            package = self.packages[package_id]
            start_package = (package[1], package[2])
            move_path = self.get_action(pos_robot, start_package)
            move = 'S' if len(move_path) == 0 else move_path[0]
            pkg_act = 1 if len(move_path) <= 1 else 0
            actions[robot_id] = (str(move), str(pkg_act))

        # Vì ưu tiên giao gói hàng chưa đến hạn, nên còn nhiều gói hàng hết deadline chưa được giao
        # Sẽ để những con robot trạng thái S đi nhặt

        # print(f"Start Actions : {actions}")

        # Cập nhật vị trí robot của state hiện tại vào bộ nhớ
        for i in range(len(robots)):
            self.robots[i] = robots[i]

        old_pos = {} # Ánh xạ vị trí có robot đang đứng đến id của robot đó
        new_pos = {} # Ánh xạ từ 1 vị trí đến danh sách id các robot muốn tới vị trí đó

        # Lưu thông tin về robot hiện tại và dự định
        for i in range(len(actions)):
            pos_robot = (robots[i][0], robots[i][1])
            old_pos[pos_robot] = i
            next_pos_robot = compute_valid_position(map, pos_robot, actions[i][0])

            # Kiểm tra vị trí muốn tới có trong danh sách chưa, nếu chưa thì tạo 1 mảng để lưu các id robot
            if next_pos_robot not in new_pos:
                new_pos[next_pos_robot] = []
            new_pos[next_pos_robot].append(pos_robot)

        # Tìm tất cả chu trình sẽ xảy ra
        cycles_list, actions_list = find_all_cycle(map, robots, actions)

        # Duyệt qua từng chu trình để phá trạng thái này
        for (element_robot, element_action) in zip(cycles_list, actions_list):
            # print(f"Cycle includes robot: {element_robot} and corresponding action: {element_action}")

            check = False # Biến kiểm tra xem có phá trạng thái chu trình bằng cách thay đổi action của 1 robot chưa
            for i in range(len(element_action)):
                pos_robot = (element_robot[i][0], element_robot[i][1])
                next_pos_robot = compute_valid_position(map, pos_robot, element_action[i][0])

                # Vì nó là chu trình, nên không cần xét vị trí mới có thuộc các tập không (chắc chắn phải thuộc tập hợp)
                moves = ['L', 'R', 'U', 'D']
                # print(element_action[i][0])
                moves.remove(element_action[i][0])
                # random.shuffle(moves) # Có thể dùng

                # Duyệt từng hướng di chuyển xem có thay đổi được action đang xét không
                for move in moves:
                    new_pos_robot = compute_valid_position(map, pos_robot, move)
                    if new_pos_robot not in old_pos and new_pos_robot not in new_pos:
                        new_pos[new_pos_robot] = [pos_robot] # Có thể gán bằng bất cứ số nào, chỉ ần để new_pos_robot có trong new_pos
                        new_pos[next_pos_robot].remove(pos_robot)
                        check = True

                        for j in range(len(robots)):
                            if pos_robot == (robots[j][0], robots[j][1]):
                                actions[j] = (move, element_action[i][1])
                        break

                # Nếu đã thay đổi thành công 1 action trong cycle thì thoát khỏi cycle luôn (tránh thay đổi tất cả action thì vô nghĩa)
                if check:
                    break

        # print(f"Actions after process cycles: {actions}")

        # Xử lý những robot có thể gây chắn đường khi ở trạng thái
        for i in range(len(actions)):
            pos_robot = (robots[i][0], robots[i][1])
            if actions[i][0] == 'S' and actions[i][1] != '1':
                if len(new_pos[pos_robot]) > 1: # Có robot khác muốn đi tới vị trí này
                    moves = ['L', 'R', 'U', 'D']
                    # random.shuffle(moves)

                    # Duyệt từng hướng di chuyển xem có thay đổi được action đang xét không
                    for move in moves:
                        new_pos_robot = compute_valid_position(map, pos_robot, move)
                        if new_pos_robot not in old_pos and new_pos_robot not in new_pos:
                            actions[i] = (move, actions[i][1])
                            new_pos[new_pos_robot] = [pos_robot]
                            break

        self.last_move = actions

        # print(f"Robots are in: {self.robots}")
        # print(f"Final Actions is: {actions}")
        return actions

# Main File

In [12]:
if __name__=="__main__":
    configs = [
        {'map': 'map1.txt', 'num_agents': 5, 'n_packages': 100},
        {'map': 'map2.txt', 'num_agents': 5, 'n_packages': 100},
        {'map': 'map3.txt', 'num_agents': 5, 'n_packages': 500},
        {'map': 'map4.txt', 'num_agents': 10, 'n_packages': 500},
        {'map': 'map5.txt', 'num_agents': 10, 'n_packages': 1000},
    ]

    seeds = [10, 42, 2025, 3407, 11711]
    maps = ['map1.txt', 'map2.txt', 'map3.txt', 'map4.txt', 'map5.txt']

    results = []
    
    for seed in seeds:
        for i, config in enumerate(configs):
            sys.argv = [
                'main.py',
                '--seed', str(seed),
                '--max_steps', '1000',
                '--max_time_steps', '1000',
                '--map', f"/kaggle/input/marl-map/{config['map']}",
                '--num_agents', str(config['num_agents']),
                '--n_packages', str(config['n_packages'])
            ]
            parser = argparse.ArgumentParser()
            parser.add_argument("--num_agents", type=int, help="Number of agents")
            parser.add_argument("--n_packages", type=int, help="Number of packages")
            parser.add_argument("--max_steps", type=int, help="Maximum number of steps per episode")
            parser.add_argument("--seed", type=int, help="Random seed for reproducibility")
            parser.add_argument("--max_time_steps", type=int, help="Maximum time steps for the environment")
            parser.add_argument("--map", type=str, help="Map name")
        
            args, unknown = parser.parse_known_args()
            np.random.seed(args.seed)

            # Greedy (baseline)
            env = Environment(map_file=args.map, max_time_steps=args.max_time_steps,
                              n_robots=args.num_agents, n_packages=args.n_packages,
                              seed = args.seed) 
            state = env.reset()
            agents = GreedyAgents()
            agents.init_agents(state)
    
            done = False
            t = 0
            max_reward = 0
            while not done:
                actions = agents.get_actions(state)
                next_state, reward, done, infos = env.step(actions)
                max_reward = max(max_reward, env.total_reward)
                state = next_state
                t += 1

            results.append({
                "seed": args.seed,
                "version": 'baseline',
                "map": config["map"],
                "result": infos['total_reward']
            })

            # Version 1
            env = Environment(map_file=args.map, max_time_steps=args.max_time_steps,
                              n_robots=args.num_agents, n_packages=args.n_packages,
                              seed = args.seed) 
            state = env.reset()
            agents = AgentsVersion1()
            agents.init_agents(state)
    
            done = False
            t = 0
            max_reward = 0
            while not done:
                actions = agents.get_actions(state)
                next_state, reward, done, infos = env.step(actions)
                max_reward = max(max_reward, env.total_reward)
                state = next_state
                t += 1

            results.append({
                "seed": args.seed,
                "version": 1,
                "map": config["map"],
                "result": infos['total_reward']
            })

            # Version2
            env = Environment(map_file=args.map, max_time_steps=args.max_time_steps,
                              n_robots=args.num_agents, n_packages=args.n_packages,
                              seed = args.seed)
            state = env.reset()
            agents = AgentsVersion2()
            agents.init_agents(state)
    
            done = False
            t = 0
            max_reward = 0
            while not done:
                actions = agents.get_actions(state)
                next_state, reward, done, infos = env.step(actions)
                max_reward = max(max_reward, env.total_reward)
                state = next_state
                t += 1

            results.append({
                "seed": args.seed,
                "version": 2,
                "map": config["map"],
                "result": infos['total_reward']
            })

            # Version 3
            env = Environment(map_file=args.map, max_time_steps=args.max_time_steps,
                              n_robots=args.num_agents, n_packages=args.n_packages,
                              seed = args.seed)
            state = env.reset()
            agents = AgentsVersion3()
            agents.init_agents(state)
    
            done = False
            t = 0
            max_reward = 0
            while not done:
                actions = agents.get_actions(state)
                next_state, reward, done, infos = env.step(actions)
                max_reward = max(max_reward, env.total_reward)
                state = next_state
                t += 1

            results.append({
                "seed": args.seed,
                "version": 3,
                "map": config["map"],
                "result": infos['total_reward']
            })

            # Version 4
            env = Environment(map_file=args.map, max_time_steps=args.max_time_steps,
                              n_robots=args.num_agents, n_packages=args.n_packages,
                              seed = args.seed)
            state = env.reset()
            agents = AgentsVersion4()
            agents.init_agents(state)
    
            done = False
            t = 0
            max_reward = 0
            while not done:
                actions = agents.get_actions(state)
                next_state, reward, done, infos = env.step(actions)
                max_reward = max(max_reward, env.total_reward)
                state = next_state
                t += 1

            results.append({
                "seed": args.seed,
                "version": 4,
                "map": config["map"],
                "result": infos['total_reward']
            })

            # version 5
            env = Environment(map_file=args.map, max_time_steps=args.max_time_steps,
                              n_robots=args.num_agents, n_packages=args.n_packages,
                              seed = args.seed)
            state = env.reset()
            agents = AgentsVersion5()
            agents.init_agents(state)
    
            done = False
            t = 0
            max_reward = 0
            while not done:
                actions = agents.get_actions(state)
                next_state, reward, done, infos = env.step(actions)
                max_reward = max(max_reward, env.total_reward)
                state = next_state
                t += 1

            results.append({
                "seed": args.seed,
                "version": 5,
                "map": config["map"],
                "result": infos['total_reward']
            })

            # Version 6
            env = Environment(map_file=args.map, max_time_steps=args.max_time_steps,
                              n_robots=args.num_agents, n_packages=args.n_packages,
                              seed = args.seed)            
            state = env.reset()
            agents = AgentsVersion6()
            agents.init_agents(state)
    
            done = False
            t = 0
            max_reward = 0
            while not done:
                actions = agents.get_actions(state)
                next_state, reward, done, infos = env.step(actions)
                max_reward = max(max_reward, env.total_reward)
                state = next_state
                t += 1

            results.append({
                "seed": args.seed,
                "version": 6,
                "map": config["map"],
                "result": infos['total_reward']
            })
            
            # f.write(f"Total time steps: {infos['total_time_steps']}\n")
            # f.write(f"Total reward: {infos['total_reward']}\n")
            # f.write(f"The max reward can: {max_reward}\n")
            # f.write(f"Args: {args}\n")
    
            
            # print(args)
    #         break
    #     break

    df = pd.DataFrame(results)
    
    pivot_df = df.pivot_table(index=['seed', 'version'], columns='map', values='result')
    pivot_df = pivot_df.fillna(0)
    pivot_df.to_csv('results.csv')
    
    print(pivot_df)

    
    # maps = '/kaggle/input/marl-map'
    # for map in os.listdir(maps):
    #     with open("map.txt", "w") as f:
    #         start_time = time.time()
    #         n = 1000
    #         list_reward = []
        
        
    #         for seed in [10, 42, 2025, 3407, 11711]:
    #             f.write(f"Start seed = {seed}\n")
    #             seed_time = time.time()
    #             parser = argparse.ArgumentParser()
    #             parser.add_argument("--num_agents", type=int, default=5, help="Number of agents")
    #             parser.add_argument("--n_packages", type=int, default=100, help="Number of packages")
    #             parser.add_argument("--max_steps", type=int, default=1000, help="Maximum number of steps per episode")
    #             parser.add_argument("--seed", type=int, default=seed, help="Random seed for reproducibility")
    #             parser.add_argument("--max_time_steps", type=int, default=1000, help="Maximum time steps for the environment")
    #             parser.add_argument("--map", type=str, default="/kaggle/input/marl-map/map3.txt", help="Map name")
            
    #             args, unknown = parser.parse_known_args()
    #             np.random.seed(args.seed)
    #             env = Environment(map_file=args.map, max_time_steps=args.max_time_steps,
    #                               n_robots=args.num_agents, n_packages=args.n_packages,
    #                               seed = args.seed)
                
                
    #             state = env.reset()
    #             agents = AgentsVersion3()
    #             agents.init_agents(state)
        
    #             done = False
    #             t = 0
    #             max_reward = 0
    #             while not done:
    #                 actions = agents.get_actions(state)
    #                 next_state, reward, done, infos = env.step(actions)
    #                 max_reward = max(max_reward, env.total_reward)
    #                 state = next_state
    #                 t += 1
    
    #             list_reward.append(infos['total_reward'])
                
    #             f.write(f"Total time steps: {infos['total_time_steps']}\n")
    #             f.write(f"Total reward: {infos['total_reward']}\n")
    #             f.write(f"The max reward can: {max_reward}\n")
    #             f.write(f"Args: {args}\n")
        
    #             count_delivered = sum(1 for pack in env.packages if pack.status == "delivered")
    #             f.write(f"Number package delivered: {count_delivered}\n")
    #             f.write(f"Number package transited: {len(agents.transited_packages)}\n")
    #             f.write(f"Finish run seed = {seed} in {time.time() - seed_time:.4f} seconds\n\n")
    #             break
            
    #         f.write(f"\nEpisode finished\n")
    #         f.write(f"List reward in {n} runs: {list_reward}\n")
    #         f.write(f"Min: {np.min(list_reward)}\n")
    #         f.write(f"Max: {np.max(list_reward)}\n")
    #         f.write(f"Mean: {np.mean(list_reward)}\n")
    #         f.write(f"Finish 5 seed in {time.time() - start_time:.4f} seconds\n")
    #         break
    #     break

State robot:  [(2, 8, 0), (5, 2, 0), (1, 6, 0), (8, 4, 0), (4, 6, 0)]
N robots =  5
Actions =  [('L', '0'), ('L', '1'), ('D', '0'), ('L', '0'), ('L', '0')]
[2, 4, 2, 3, 6]
State robot:  [(2, 7, 0), (5, 1, 4), (2, 6, 0), (8, 3, 0), (4, 5, 0)]
N robots =  5
Actions =  [('L', '0'), ('D', '0'), ('L', '0'), ('L', '1'), ('L', '1')]
[2, 4, 2, 3, 6]
State robot:  [(2, 6, 0), (6, 1, 4), (2, 5, 0), (8, 2, 3), (4, 4, 6)]
N robots =  5
Actions =  [('L', '0'), ('R', '2'), ('L', '1'), ('U', '0'), ('D', '0')]
[2, 4, 2, 3, 6]
State robot:  [(2, 5, 0), (6, 2, 0), (2, 4, 2), (7, 2, 3), (5, 4, 6)]
N robots =  5
Actions =  [('L', '1'), ('D', '0'), ('D', '0'), ('U', '0'), ('D', '0')]
[2, 3, 2, 3, 6]
State robot:  [(2, 4, 0), (6, 2, 0), (3, 4, 2), (7, 2, 3), (6, 4, 6)]
N robots =  5
Actions =  [('S', '1'), ('D', '0'), ('D', '0'), ('U', '0'), ('R', '0')]
[2, 3, 2, 3, 6]
State robot:  [(2, 4, 0), (6, 2, 0), (4, 4, 2), (7, 2, 3), (6, 5, 6)]
N robots =  5
Actions =  [('S', '1'), ('D', '0'), ('D', '0'), ('U', '0

# Visualize File

In [13]:
# import numpy as np
# import matplotlib.pyplot as plt
# from matplotlib.patches import Circle, Patch
# from matplotlib.colors import ListedColormap
# import matplotlib.animation as animation
# from IPython.display import HTML
# from ipywidgets import interact, IntSlider
# import argparse

# class DeliveryVisualizer:
#     def __init__(self, env):
#         self.env = env
#         self.map = np.array(env.grid)
#         self.fig, self.ax = plt.subplots(figsize=(10, 6))
#         self.robot_markers = []
#         self.package_markers = {}
#         self.time_text = None
#         self.reward_text = None
#         self.state_history = []
#         self.reward_history = []
#         self.actions = []

#         self.colors = {
#             'wall': 'black',
#             'free': 'white',
#             'robot': 'blue',
#             'package_waiting': 'green',
#             'package_transit': 'orange',
#             'package_delivered': 'red',
#             'target': 'purple'
#         }

#         self.setup_plot()
#         self._create_legend()

#     def setup_plot(self):
#         cmap = ListedColormap(['white', 'black'])

#         self.ax.imshow(self.map, cmap=cmap)
#         self.ax.grid(True, color='gray', linestyle='-', linewidth=0.5)
#         self.ax.set_title('Multi-Agent Package Delivery Simulation')
#         self.ax.set_xlabel('Column')
#         self.ax.set_ylabel('Row')

#         self.time_text = self.ax.text(0.02, 0.95, 'Time Step: 0',
#                                       transform=self.ax.transAxes,
#                                       fontsize=12, fontweight='bold',
#                                       bbox=dict(facecolor='white', alpha=0.7))
#         self.reward_text = self.ax.text(0.02, 0.90, 'Total Reward: 0.00',
#                                         transform=self.ax.transAxes,
#                                         fontsize=12, fontweight='bold',
#                                         bbox=dict(facecolor='white', alpha=0.7))

#     # Bảng chú thích
#     def _create_legend(self):
#         self.fig.subplots_adjust(right=0.8)
#         legend_elements = [
#             Patch(facecolor='black', edgecolor='black', label='Wall'),
#             Patch(facecolor='white', edgecolor='gray', label='Free Space'),
#             Circle((0, 0), radius=1, facecolor=self.colors['robot'], edgecolor='black', label='Robot'),
#             Patch(facecolor=self.colors['package_waiting'], edgecolor='black', alpha=0.5, label='Waiting Package'),
#             Patch(facecolor=self.colors['package_transit'], edgecolor='black', alpha=0.5, label='Package in Transit'),
#             Patch(facecolor=self.colors['package_delivered'], edgecolor='black', alpha=0.5, label='Delivered Package'),
#             Patch(facecolor=self.colors['target'], edgecolor='black', alpha=0.5, label='Target Location'),
#             Line2D([0], [0], marker='$R1$', color='w', markerfacecolor='black', markersize=15, label='Robot ID'),
#             Line2D([0], [0], marker='$P1$', color='w', markerfacecolor='black', markersize=15, label='Package ID'),
#             Line2D([0], [0], marker='$T1$', color='w', markerfacecolor='black', markersize=15, label='Target ID')
#         ]
#         self.ax.legend(handles=legend_elements, loc='center left',
#                        bbox_to_anchor=(1.02, 0.5), fontsize=10,
#                        title="Map Legend", frameon=True)

#     def update_display(self, state, reward, actions=None):
#         for marker in self.robot_markers:
#             marker.remove()
#         self.robot_markers = []

#         self.time_text.set_text(f'Time Step: {state["time_step"]}')
#         self.reward_text.set_text(f'Total Reward: {reward}')

#         for i, robot in enumerate(state['robots']):
#             row, col, carrying = robot[0] - 1, robot[1] - 1, robot[2]
#             robot_circle = Circle((col, row), 0.3, color=self.colors['robot'],alpha=0.7, zorder=3)
#             self.ax.add_patch(robot_circle)
#             self.robot_markers.append(robot_circle)
#             robot_text = self.ax.text(col, row, f'R{i}', ha='center', va='center', color='white', fontsize=8, zorder=4)
#             self.robot_markers.append(robot_text)

#             if actions and i < len(actions):
#                 move_direction = actions[i][0] 
#                 dx, dy = 0, 0
#                 if move_direction == 'U':
#                     dx, dy = 0, -0.5
#                 elif move_direction == 'D':
#                     dx, dy = 0, 0.5
#                 elif move_direction == 'L':
#                     dx, dy = -0.5, 0
#                 elif move_direction == 'R':
#                     dx, dy = 0.5, 0
                    
#                 if move_direction != 'S':
#                     arrow = self.ax.arrow(col, row, dx, dy, head_width=0.2,
#                                           head_length=0.2, fc='yellow', ec='black',
#                                           zorder=5, alpha=0.8)
#                     self.robot_markers.append(arrow)

#             if carrying > 0:
#                 carried_text = self.ax.text(col, row - 0.4, f'P{carrying}',
#                                             ha='center', va='center', color='black',
#                                             fontsize=7, zorder=4)
#                 self.robot_markers.append(carried_text)

#         self.process_packages(state)
#         self.fig.canvas.draw()

#     def process_packages(self, state):
#         current_time = state['time_step']
#         # Tất cả packages của env
#         env_packages = self.env.packages

#         for pkg_id in list(self.package_markers.keys()):
#             # Trả về đối tượng đầu tiên
#             pkg = next((p for p in env_packages if p.package_id == pkg_id), None)
#             # Ẩn những package chưa được giao
#             if pkg and pkg.start_time > current_time and pkg.status == 'None':
#                 # Remove the visual elements if they exist
#                 marker = self.package_markers[pkg_id]
#                 marker['pickup'].remove()
#                 marker['target'].remove()
#                 marker['pickup_text'].remove()
#                 marker['target_text'].remove()
#                 del self.package_markers[pkg_id]


#         for pkg in env_packages:
#             pkg_id = pkg.package_id
#             # Bỏ qua k hiển thị những package chưa xuất hiện
#             if pkg.start_time > current_time and pkg.status == 'None':
#                 continue

#             start_row, start_col = pkg.start[0], pkg.start[1]
#             target_row, target_col = pkg.target[0], pkg.target[1]
#             status = pkg.status  # 'None', 'waiting', 'in_transit', or 'delivered'


#             if pkg_id not in self.package_markers:
#                 pickup_marker = Rectangle((start_col - 0.4, start_row - 0.4), 0.8, 0.8,
#                                           color=self.colors['package_waiting'], alpha=0.5, zorder=2)
#                 self.ax.add_patch(pickup_marker)
#                 target_marker = Rectangle((target_col - 0.4, target_row - 0.4), 0.8, 0.8,
#                                           color=self.colors['target'], alpha=0.3, zorder=1)
#                 self.ax.add_patch(target_marker)
#                 pickup_text = self.ax.text(start_col, start_row, f'P{pkg_id}',
#                                            ha='center', va='center', color='black',
#                                            fontsize=7, zorder=2)
#                 target_text = self.ax.text(target_col, target_row, f'T{pkg_id}',
#                                            ha='center', va='center', color='black',
#                                            fontsize=7, zorder=1)

#                 self.package_markers[pkg_id] = {
#                     'pickup': pickup_marker,
#                     'target': target_marker,
#                     'pickup_text': pickup_text,
#                     'target_text': target_text,
#                     'status': status
#                 }

#             marker = self.package_markers[pkg_id]
#             current_status = marker['status']

#             if status != current_status:
#                 marker['status'] = status
#                 if status == 'in_transit':
#                     marker['pickup'].set_color(self.colors['package_transit'])
#                 elif status == 'delivered':
#                     marker['target'].set_color(self.colors['package_delivered'])
#                 elif status == 'waiting':
#                     marker['pickup'].set_color(self.colors['package_waiting'])
                    

#     def run_and_record(self, env, agents, steps=100):
#         state = env.reset()
#         agents.init_agents(state)
        
#         self.state_history = []
#         self.reward_history = []
        
#         done = False
#         t = 0

#         while not done and t < steps:
#             actions = agents.get_actions(state)
#             self.state_history.append(state.copy())
#             self.reward_history.append(round(env.total_reward, 2))
#             self.actions.append(actions)
#             next_state, reward, done, infos = env.step(actions)
#             state = next_state
#             t += 1

#         # self.state_history.append(state)
#         # self.reward_history.append(round(env.total_reward, 2))
#         # self.actions.append(actions)

#     def create_animation(self, fps=5):
#         def animate(i):
#             # self.ax.clear() 
#             # self.setup_plot() 
#             self._create_legend()
#             if i < len(self.state_history):
#                 self.update_display(self.state_history[i], self.reward_history[i], self.actions[i])
#             return self.robot_markers + list(self.package_markers.values())

#         ani = animation.FuncAnimation(self.fig, animate, frames=len(self.state_history),
#                                       interval=1000 / fps, blit=False)
#         return HTML(ani.to_jshtml())

#     def interactive_viewer(self):
#         def view_step(step):
#             self.update_display(self.state_history[step], self.reward_history[step])
#             self.fig.canvas.draw() 
            
#         slider = IntSlider(min=0, max=len(self.state_history)-1, step=1, value=0, description='Step:')
#         interact(view_step, step=slider)

# # Dùng từ notebook

# def visualize_delivery(map_file='map5.txt', num_agents=5, n_packages=10, max_steps=100, seed=2025):
#     env = Environment(map_file=map_file, max_time_steps=max_steps,
#                       n_robots=num_agents, n_packages=n_packages, seed=seed)
#     agents = AgentsVersion6()
#     visualizer = DeliveryVisualizer(env)
#     visualizer.run_and_record(env, agents, steps=max_steps)
#     # return visualizer.interactive_viewer()
#     # return visualizer.create_animation()
#     return visualizer


In [14]:
# parser = argparse.ArgumentParser()
# parser.add_argument("--num_agents", type=int, default=10, help="Number of agents")
# parser.add_argument("--n_packages", type=int, default=1000, help="Number of packages")
# parser.add_argument("--max_steps", type=int, default=1000, help="Maximum number of steps per episode")
# parser.add_argument("--seed", type=int, default=2025, help="Random seed for reproducibility")
# parser.add_argument("--max_time_steps", type=int, default=1000, help="Maximum time steps for the environment")
# parser.add_argument("--map", type=str, default="/kaggle/input/marl-map/map5.txt", help="Map name")

# args, unknown = parser.parse_known_args()
# np.random.seed(args.seed)

# vis = visualize_delivery(
#     map_file=args.map,
#     num_agents=args.num_agents,
#     n_packages=args.n_packages,
#     max_steps=args.max_steps,
#     seed=args.seed
# )

# display(vis.create_animation())